# Maxent modeling results
S. Filhol, June 2022

Script to add to ML results the Maxent model. 

In [1]:
import xarray as xr
import rasterio
import rioxarray

import warnings
warnings.filterwarnings("ignore")


In [2]:
thresholds = {
    'model_-2':-2,
    'model_-2_5':-2.5,
    'model_-3':-3
}
encode = {
        "permafrost_probability": {"compression": "gzip", "compression_opts": 9},
        "elevation": {"compression": "gzip", "compression_opts": 9},
        "slope": {"compression": "gzip", "compression_opts": 9},
        "mask": {"compression": "gzip", "compression_opts": 9},
        "solar": {"compression": "gzip", "compression_opts": 9},
        "ndvi": {"compression": "gzip", "compression_opts": 9},
        "curv": {"compression": "gzip", "compression_opts": 9},
        "snow_prob_median": {"compression": "gzip", "compression_opts": 9},    
    }

ML_config = 'OUTPUT_WEIGHTED_v5'

for massif in ['fagaras-iezer', 'retezat', 'parang']:
    print('---> {} massif'.format(massif))
    root_maxent = './outputs/maxent/{}/'.format(massif)
    root_ML = './outputs'
    ds = xr.open_dataset('{}{}_all.nc'.format(root_ML, massif))
    for thres in thresholds.keys():
        print('-> adding threshold {}'.format(thresholds.get(thres)))
        file = root_maxent + thres + '/prez.asc'

        xds = xr.open_dataset(file, engine='rasterio')
        x = xds.drop(['band','spatial_ref'])
        x = x.assign_coords({'threshold':thresholds.get(thres), 'model':'Maxent'})
        x = x.expand_dims({'threshold':1, 'model':1})
        x = x.rename({'band_data':'permafrost_probability'})
        x = x.sel(band=0, drop=True)

        ds = xr.merge([ds,x])
    fout = root_ML + '{}_all_maxent.nc'.format(massif)
    ds.to_netcdf(fout, 'w', encoding=encode, engine='h5netcdf')
    ds = None
    
    

---> fagaras-iezer massif
-> adding threshold -2
-> adding threshold -2.5
-> adding threshold -3
---> retezat massif
-> adding threshold -2
-> adding threshold -2.5
-> adding threshold -3
---> parang massif
-> adding threshold -2
-> adding threshold -2.5
-> adding threshold -3


In [5]:
pwd

'/home/simonfi/github/ClimaLAND/permafrost_modeling'